In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import shapefile
from pandas.plotting import table
import matplotlib as mpl
import matplotlib.pyplot as plt
from datetime import datetime
import geopandas as gpd
import folium
from datetime import date
from folium.plugins import FastMarkerCluster
import os
import plotly.graph_objects as go
# a nice way of filtering out deprecated warnings
import warnings
import kaleido

warnings.filterwarnings("ignore")
os.chdir('../raw_data')

In [2]:
fname = ["april_taxi.csv","may_taxi.csv","june_taxi.csv","july_taxi.csv","august_taxi.csv",
         "september_taxi.csv", "october_taxi.csv", 
         "november_taxi.csv","december_taxi.csv"]
months = ["april", "may", "june", "july", "august", "september", "october", "november", "december"]


In [3]:
march_df = pd.read_csv("../raw_data/march_taxi.csv")

In [4]:
march_df = march_df.loc[(pd.DatetimeIndex(march_df["tpep_pickup_datetime"]).month == 3) & 
              (pd.DatetimeIndex(march_df["tpep_pickup_datetime"]).day >=8)]

In [5]:

april_df = pd.read_csv("../raw_data/april_taxi.csv")
may_df = pd.read_csv("../raw_data/may_taxi.csv")
june_df = pd.read_csv("../raw_data/june_taxi.csv")
july_df = pd.read_csv("../raw_data/july_taxi.csv")
august_df = pd.read_csv("../raw_data/august_taxi.csv")
september_df = pd.read_csv("../raw_data/september_taxi.csv")
october_df = pd.read_csv("../raw_data/october_taxi.csv")
november_df = pd.read_csv("../raw_data/november_taxi.csv")
december_df = pd.read_csv("../raw_data/december_taxi.csv")



In [6]:
all_months_df = pd.concat([march_df, april_df, may_df, june_df, july_df, august_df, september_df,
                             october_df, november_df, december_df])

In [7]:
sf = gpd.read_file("../raw_data/taxi_zones.shp")
zone = pd.read_csv("../raw_data/taxi+_zone_lookup.csv")

# Convert the geometry shape to to latitude and longitude
# Reproduced from Lab 2 for MAST30034
sf['geometry'] = sf['geometry'].to_crs("+proj=longlat +ellps=WGS84 +datum=WGS84 +no_defs")
pickup_gdf = gpd.GeoDataFrame(pd.merge(all_months_df, sf, left_on='PULocationID', right_on='LocationID')).drop('PULocationID',axis=1)
pickup_gdf['count'] = 1

In [8]:
total_rides = pickup_gdf.groupby(["LocationID"]).count()[['count']].reset_index()

In [9]:
pickup_geoJSON = pickup_gdf[['LocationID','geometry']].drop_duplicates('LocationID').to_json()

In [10]:
# Plot total pickups per taxi zone
m_pickups = folium.Map(location=[40.66, -73.94], tiles="Stamen Terrain", zoom_start=10)

# Adapted from lab 2 of MAST30034
# Plot pickup data
folium.Choropleth(
    geo_data=pickup_geoJSON, # geoJSON 
    name='choropleth', # name of plot
    data= total_rides, # data source
    columns=['LocationID','count'], # the columns required
    key_on='properties.LocationID', # this is from the geoJSON's properties
    fill_color='OrRd', # color scheme
    fill_opacity=0.9,
    line_opacity=0.5,
    legend_name='Total Pickups' # legend title
).add_to(m_pickups)

m_pickups.save('../plots/' + 'TotalPickups.html')
m_pickups


In [11]:
# Plot descriptive statistics in table
fig = go.Figure(data=[go.Table(
    header=dict(values=['Statistic','Passenger Count', ' Trip Distance'],
                line_color='darkslategray',
                fill_color='lightskyblue',
                align='left'),
    cells=dict(values=[["count", "mean", "standard deviation", "minimum",
                       "25%", "50%", "75", "maximum"], all_months_df['passenger_count'].describe().apply("{0:.3f}".format), 
                       all_months_df['trip_distance'].describe().apply("{0:.3f}".format)], 
               line_color='darkslategray',
               fill_color='lavender',
               align='left'))
])

# fig.update_layout(width=1000, height=1000)
fig.show()
fig.write_image("../plots/descriptives.png", width=500, height=500, scale = 10)

In [3]:
covid_data = pd.read_csv("../raw_data/statistic_id1109711_number-of-new-covid-19-cases-in-nyc-from-mar-8-2020-to-july-31-2021-by-day.csv")
covid_data = covid_data.rename(columns = ({"Number of new COVID-19 cases in NYC from Mar. 8, 2020 to July 31, 2021, by day": "Date",
                             "Unnamed: 1": "Cases"}))
covid_data = covid_data.drop([0,1])
covid_data["Date"] = pd.to_datetime(covid_data["Date"], format = "%m/%d/%y")
covid_data = covid_data.loc[pd.DatetimeIndex(covid_data["Date"]).year <2021]

In [4]:
covid_data["Cases"].describe()

count     299.000000
mean     1337.277592
std      1476.181151
min        21.000000
25%       314.000000
50%       584.000000
75%      2047.500000
max      6353.000000
Name: Cases, dtype: float64